In [12]:
import os
import sys
sys.path.append(os.path.abspath('../../../..'))

import numpy as np
import pandas as pd

import h5py
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.cluster.hierarchy import linkage, dendrogram, leaves_list
from scipy.stats import zscore
# # step one, dannce alignment


# from utlis.corr_utlis.processed_syned_load import load_filtered_data_from_h5

rec_path = '/data/big_rim/rsync_dcc_sum/Oct3V1/2024_10_25/20241002PMCr2_17_05'

hdf5_file_path = os.path.join(rec_path, 'MIR_Aligned/aligned_predictions_with_ca_and_dF_F.h5')

# Load the DataFrame from the HDF5 file
df_merged_with_dF_F = pd.read_hdf(hdf5_file_path, key='df')

# Assuming df_merged_with_dF_F is already loaded
# Extract columns that correspond to neurons
neuron_columns = [col for col in df_merged_with_dF_F.columns if col.startswith('dF_F_roi')]
neuron_activity = df_merged_with_dF_F[neuron_columns].values  # shape: (timepoints, neurons)

# Transpose to get shape: (neurons, timepoints)
neuron_activity = neuron_activity.T

# Step to drop low-variance neurons (reduce false positives)
neuron_variances = np.var(neuron_activity, axis=1)  # Variance for each neuron
threshold = np.percentile(neuron_variances, 5)      # Keep top 95% variance
high_variance_indices = neuron_variances > threshold  # Mask for neurons to keep

# Filter neuron activity and neuron column names
neuron_activity_filtered = neuron_activity[high_variance_indices, :]
filtered_neuron_columns = [col for i, col in enumerate(neuron_columns) if high_variance_indices[i]]

# Optional: Z-score normalization along each neuron's time course
neuron_activity_normalized = zscore(neuron_activity_filtered, axis=1)
# 'correlation' is often a good metric for neural activity, but you can try 'euclidean'.
# 'average' linkage is a common choice, but feel free to experiment (e.g., 'ward', 'complete').
# Perform hierarchical clustering on the filtered and normalized data
Z = linkage(neuron_activity_normalized, method='average', metric='correlation')

df_new = df_merged_with_dF_F.copy()
df_new = df_new.reset_index()
time = df_new['timestamp_ms_mini']



In [ ]:
head_keypoints = [1, 2, 3, 4]  # Example: EarL, EarR, Snout, SpineF
head_coords = df_merged_with_dF_F[[f"kp{idx}_{axis}" for idx in head_keypoints for axis in ['x', 'y', 'z']]].copy()


if 'com_x' in df_merged_with_dF_F.columns and 'com_y' in df_merged_with_dF_F.columns and 'com_z' in df_merged_with_dF_F.columns:
    head_coords_ego = df_merged_with_dF_F[
        [f"kp{idx}_{axis}" for idx in head_keypoints for axis in ['x', 'y', 'z']]
    ].copy()

    for axis in ['x', 'y', 'z']:
        com_col = f'com_{axis}'
        if com_col in df_merged_with_dF_F.columns:
            head_coords_ego[[f"kp{idx}_{axis}" for idx in head_keypoints]] -= df_merged_with_dF_F[com_col].values[:, None]
        else:
            print(f"Warning: {com_col} not found. Cannot adjust for egocentric {axis} coordinates.")
else:
    print("COM columns (com_x, com_y, com_z) not found. Using absolute coordinates.")


In [31]:
def connectivity(path: str, skeleton_name: str):
    """ 
    MIR QI TAKEN/Adapted FROM JOSH WU, FROM DAPPY/NEUROPOSELIB
    DEPRECATED

    Reads in connectivity from skeleton.py file

    Parameters
    ----------
    path : str
        Path to skeleton/connectivity Python file.
    skeleton_name : str
        Name of skeleton type to load in.

    Returns
    -------
    connectivity: Connectivity object
        Connectivity class object containing designated skeleton information
    """
    if path.endswith(".py"):
        import importlib.util

        mod_spec = importlib.util.spec_from_file_location("connectivity", path)
        con = importlib.util.module_from_spec(mod_spec)
        mod_spec.loader.exec_module(con)

        joint_names = con.JOINT_NAME_DICT[skeleton_name]  # joint names
        colors = con.COLOR_DICT[skeleton_name]  # color to be plotted for each linkage
        links = con.CONNECTIVITY_DICT[skeleton_name]  # joint linkages
        angles = con.JOINT_ANGLES_DICT[skeleton_name]  # angles to calculate

    # connectivity = Connectivity(
    #     joint_names=joint_names, colors=colors, links=links, angles=angles
    # )

    connectivity = {
            "joint_names": joint_names,
            "colors": colors,
            "links": links,
            "angles": angles,
        }

    return connectivity




# def compute_mean_connection_lengths(df, connectivity, offset=1):
#     """
#     Computes the average length of specified connections for each row in df.

#     Parameters
#     ----------
#     df : pd.DataFrame
#         A DataFrame containing columns named like 'kp1_x', 'kp1_y', 'kp1_z', etc.
#     connectivity : list of tuples
#         A list of (start_keypoint, end_keypoint) pairs in 0-based indexing.
#     offset : int
#         The value to add to the connectivity keypoints to match the DataFrame columns
#         (since your DataFrame is 1-based).

#     Returns
#     -------
#     list
#         A list of the average connection lengths for each row in df.
#     """
#     mean_lengths_per_row = []
    
#     for _, row in df.iterrows():
#         distances = []
#         for (kpA, kpB) in connectivity:
#             # Convert from 0-based connectivity to 1-based column naming
#             kpA_idx = kpA + offset
#             kpB_idx = kpB + offset
            
#             # Extract coordinates for the two keypoints
#             xA, yA, zA = row[f'kp{kpA_idx}_x'], row[f'kp{kpA_idx}_y'], row[f'kp{kpA_idx}_z']
#             xB, yB, zB = row[f'kp{kpB_idx}_x'], row[f'kp{kpB_idx}_y'], row[f'kp{kpB_idx}_z']
            
#             # Compute Euclidean distance
#             dist = np.sqrt((xB - xA)**2 + (yB - yA)**2 + (zB - zA)**2)
#             distances.append(dist)
        
#         # Store the mean distance for this row
#         mean_lengths_per_row.append(np.mean(distances))
    
#     return mean_lengths_per_row


def compute_mean_connection_lengths(df, connectivity_dict, offset=1):
    """
    Computes the average length of specified connections for each row in df,
    and returns the result in a dictionary format.

    Parameters
    ----------
    df : pd.DataFrame
        A DataFrame containing columns named like 'kp1_x', 'kp1_y', 'kp1_z', etc.
    connectivity_dict : dict
        A dictionary containing keypoint connectivity information, obtained from the `connectivity` function.
    offset : int, optional
        The value to add to the connectivity keypoints to match the DataFrame columns
        (since your DataFrame is 1-based), default is 1.

    Returns
    -------
    dict
        A dictionary where keys are connection labels (e.g., 'SpineF-Tail(base)'),
        and values are lists of computed distances for each row in df.
    """
    links = connectivity_dict.get("links", [])
    joint_names = connectivity_dict.get("joint_names", [])

    # Create connection labels based on joint names
    connection_labels = [
        f"{joint_names[kpA]}-{joint_names[kpB]}" for kpA, kpB in links
    ]

    # Initialize dictionary to store computed distances
    connection_distances = {label: [] for label in connection_labels}

    for _, row in df.iterrows():
        for (kpA, kpB), label in zip(links, connection_labels):
            # Convert from 0-based connectivity to 1-based column naming
            kpA_idx = kpA + offset
            kpB_idx = kpB + offset

            # Extract coordinates for the two keypoints
            xA, yA, zA = row[f'kp{kpA_idx}_x'], row[f'kp{kpA_idx}_y'], row[f'kp{kpA_idx}_z']
            xB, yB, zB = row[f'kp{kpB_idx}_x'], row[f'kp{kpB_idx}_y'], row[f'kp{kpB_idx}_z']

            # Compute Euclidean distance
            dist = np.sqrt((xB - xA) ** 2 + (yB - yA) ** 2 + (zB - zA) ** 2)
            connection_distances[label].append(dist)

    return connection_distances


def compute_joint_angles(df, connectivity_dict, offset=1):
    """
    Computes the angles formed by keypoint triplets specified in the connectivity dictionary
    for each row in the DataFrame, returning the results in a dictionary format.

    Parameters
    ----------
    df : pd.DataFrame
        A DataFrame containing columns named like 'kp1_x', 'kp1_y', 'kp1_z', etc.
    connectivity_dict : dict
        A dictionary containing keypoint connectivity information, including joint angles.
    offset : int, optional
        The value to add to the connectivity keypoints to match the DataFrame columns
        (since your DataFrame is 1-based), default is 1.

    Returns
    -------
    dict
        A dictionary where keys are angle labels (e.g., 'SpineF-SpineM-Tail(base)'),
        and values are lists of computed angles for each row in df.
    """
    angles_list = connectivity_dict.get("angles", [])
    joint_names = connectivity_dict.get("joint_names", [])

    # Create angle labels based on joint names
    angle_labels = [
        f"{joint_names[kpA]}-{joint_names[kpB]}-{joint_names[kpC]}" for kpA, kpB, kpC in angles_list
    ]

    # Initialize dictionary to store computed angles
    angle_values = {label: [] for label in angle_labels}

    for _, row in df.iterrows():
        for (kpA, kpB, kpC), label in zip(angles_list, angle_labels):
            # Convert from 0-based connectivity to 1-based column naming
            kpA_idx, kpB_idx, kpC_idx = kpA + offset, kpB + offset, kpC + offset

            # Extract coordinates for the three keypoints
            A = np.array([row[f'kp{kpA_idx}_x'], row[f'kp{kpA_idx}_y'], row[f'kp{kpA_idx}_z']])
            B = np.array([row[f'kp{kpB_idx}_x'], row[f'kp{kpB_idx}_y'], row[f'kp{kpB_idx}_z']])
            C = np.array([row[f'kp{kpC_idx}_x'], row[f'kp{kpC_idx}_y'], row[f'kp{kpC_idx}_z']])

            # Compute vectors
            v1 = A - B
            v2 = C - B

            # Normalize vectors
            v1_u = v1 / np.linalg.norm(v1)
            v2_u = v2 / np.linalg.norm(v2)

            # Compute angle using dot product and arccos
            dot_product = np.clip(np.dot(v1_u, v2_u), -1.0, 1.0)
            angle = np.arccos(dot_product)  # Angle in radians

            # Convert to degrees for better interpretation
            angle_degrees = np.degrees(angle)
            angle_values[label].append(angle_degrees)

    return angle_values


In [22]:
skeleton_info = connectivity("./skeletons.py", "mouse22_notail")
print(skeleton_info["joint_names"])
print(skeleton_info["links"])


['EarL', 'EarR', 'Snout', 'SpineF', 'SpineM', 'Tail(base)', 'Tail(mid)', 'Tail(end)', 'ForepawL', 'WristL', 'ElbowL', 'ShoulderL', 'ForepawR', 'WristR', 'ElbowR', 'ShoulderR', 'HindpawL', 'AnkleL', 'KneeL', 'HindpawR', 'AnkleR', 'KneeR,']
[(0, 1), (1, 2), (0, 2), (0, 3), (1, 3), (2, 3), (3, 4), (4, 5), (8, 9), (9, 10), (10, 11), (11, 3), (12, 13), (13, 14), (14, 15), (15, 3), (16, 17), (17, 18), (18, 4), (19, 20), (20, 21), (21, 4)]


In [ ]:


connection_distances = compute_mean_connection_lengths(df_merged_with_dF_F, skeleton_info)

# Accessing distances for a specific connection
# print(connection_distances["SpineM-Tail(base)"])  # Example output: [10.2, 9.8, 10.5]

# Iterate through all connections and print their average length across all rows
for connection, distances in connection_distances.items():
    print(f"{connection}: {np.mean(distances):.2f}")

[33.39501414803327, 32.89984336219962, 33.92236366676221, 33.417579291685904, 33.29310494415956, 33.96221063443332, 33.68898779084958, 31.35700113337541, 33.34727765220051, 31.74873998344267, 32.34621807037356, 32.58952184986896, 32.91113730011707, 32.848782589420686, 33.0071566887246, 33.3777115510837, 32.33094715453967, 29.655301657688238, 29.42452557410176, 29.842688546785404, 31.556930412322178, 30.674353458091097, 32.886109548565834, 32.879004034493896, 33.71999673858757, 32.78621555868344, 33.292880192933026, 33.53388876796229, 33.191943056731475, 31.798675560320447, 33.48916560643132, 34.016539962718255, 30.966261379363115, 31.122935787509945, 30.54825957694445, 31.193740918370942, 31.081488337887034, 30.311379569996074, 32.257215725805025, 30.2911933469461, 29.279465652090884, 29.268902764634817, 30.460046716084367, 31.11962196510223, 31.889987724100205, 32.52072208452942, 34.524312082392, 34.61199654062038, 34.54113868919318, 34.37843728321159, 33.17743751617522, 32.7251116449

In [ ]:
connection_anges = compute_joint_angles(df_merged_with_dF_F, skeleton_info)

# print(connection_anges)

{'Snout-EarR-SpineF': [87.41591258147344, 86.13731457688213, 85.09570371211112, 81.43891124207705, 73.10694946433422, 77.43930320466234, 78.79001250240194, 76.9723591753286, 77.52312398803471, 75.35921238115968, 75.115846227645, 76.33173572786151, 80.16765291705474, 85.58595262518482, 91.51031872906528, 87.9211376356438, 84.61906683344145, 77.26520271135996, 83.02435725120357, 87.58835173884864, 81.62703200614519, 69.43257330124237, 72.53791349587998, 71.07936009010129, 77.09557279312106, 84.4771174565375, 77.55315343738286, 85.0814134085013, 81.55209093176231, 80.0750893688041, 75.0296012956281, 75.65840592342859, 81.19698858519342, 74.25180315899584, 75.53168464555792, 80.35543049308522, 79.24491841441534, 90.73464183752571, 90.90783935297087, 86.83152363422978, 60.43533376071223, 62.77435541833829, 79.13014328660779, 77.25765927294529, 81.8994105031206, 86.0006437354375, 83.6064778140623, 81.88162684341465, 85.75944217163239, 78.11286001543675, 76.62351469596135, 79.73988088227046, 